In [71]:
!pip install --upgrade pip
!pip install interpret
!pip install lightgbm
!pip install xgboost
!pip install catboost

  Using cached pip-21.3.1-py3-none-any.whl (1.7 MB)
  Attempting uninstall: pip
    Found existing installation: pip 21.2.4
    Uninstalling pip-21.2.4:


ERROR: Could not install packages due to an OSError: [WinError 5] Zugriff verweigert: 'c:\\programdata\\anaconda3\\lib\\site-packages\\pip-21.2.4.dist-info\\entry_points.txt'
Consider using the `--user` option or check the permissions.

You should consider upgrading via the 'c:\programdata\anaconda3\python.exe -m pip install --upgrade pip' command.



You should consider upgrading via the 'c:\programdata\anaconda3\python.exe -m pip install --upgrade pip' command.


You should consider upgrading via the 'c:\programdata\anaconda3\python.exe -m pip install --upgrade pip' command.


You should consider upgrading via the 'c:\programdata\anaconda3\python.exe -m pip install --upgrade pip' command.


You should consider upgrading via the 'c:\programdata\anaconda3\python.exe -m pip install --upgrade pip' command.


In [72]:
!pip install shap


You should consider upgrading via the 'c:\programdata\anaconda3\python.exe -m pip install --upgrade pip' command.


In [73]:
%%javascript
IPython.OutputArea.auto_scroll_threshold = 9999;

<IPython.core.display.Javascript object>

In [74]:
import pandas as pd
from lightgbm import LGBMRegressor
from xgboost import XGBRegressor
from catboost import CatBoostRegressor
from interpret.glassbox import ExplainableBoostingRegressor
from sklearn.experimental import enable_hist_gradient_boosting
from sklearn.ensemble import HistGradientBoostingRegressor, RandomForestRegressor, ExtraTreesRegressor
from sklearn import tree
from sklearn.ensemble import GradientBoostingRegressor
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
from sklearn.datasets import make_regression
import shap
import numpy as np
from catboost import Pool

In [75]:
#X, y = make_regression(n_features=1, n_samples=150, noise=50)
#data = pd.DataFrame(data=X, columns=['X'])
#data["X2"] = X
#data["X3"] = X
#data["y"] = y

In [76]:
#fig = make_subplots(rows=1, cols=2)

#fig.append_trace(go.Scatter(y=data_full[entry], mode="lines", name='Feature 1'), row=1, col=1)
#fig.append_trace(go.Scatter(y=data_full[entry], name='Feature 2'), row=1, col=2)

In [77]:
#data.to_csv("data.csv", index=False)

In [78]:
data = pd.read_csv("data.csv", sep=",")

In [79]:
data

X        X2        X3           y
0   -0.286646 -0.286646 -0.286646    6.763356
1    0.292198  0.292198  0.292198   84.527140
2   -0.582111 -0.582111 -0.582111   52.312713
3   -0.239307 -0.239307 -0.239307   17.355994
4    1.388861  1.388861  1.388861   57.113500
..        ...       ...       ...         ...
145  0.168134  0.168134  0.168134   72.163757
146 -2.399240 -2.399240 -2.399240 -151.756926
147 -0.039827 -0.039827 -0.039827  -13.423335
148 -1.792714 -1.792714 -1.792714  -32.202962
149 -0.231555 -0.231555 -0.231555 -121.117394

[150 rows x 4 columns]

In [80]:
y = data["y"]
X = data.drop(["y"], axis=1)

In [81]:
from sklearn.model_selection import train_test_split
X_train, X_val, y_train, y_val = train_test_split(X, y, random_state=0)

In [82]:
df = pd.DataFrame(columns=[
    "model_dt_f1", 
    "model_dt_f2", 
    "model_dt_f3", 
    
    "model_rf_f1", 
    "model_rf_f2", 
    "model_rf_f3",
    
    "model_et_f1",
    "model_et_f2", 
    "model_et_f3",
    
    "model_cat_f1", 
    "model_cat_f2",
    "model_cat_f3",
    
    "model_ebm_f1_out_1",
    "model_ebm_f2_out_1",
    "model_ebm_f3_out_1",
    
    "model_ebm_f1_out_8",
    "model_ebm_f2_out_8",
    "model_ebm_f3_out_8",
    
    "model_ebm_f1_out_16",
    "model_ebm_f2_out_16",
    "model_ebm_f3_out_16",
    
    "model_ebm_f1_out_24",
    "model_ebm_f2_out_24",
    "model_ebm_f3_out_24",
    
    "model_lgb_f1",
    "model_lgb_f2",
    "model_lgb_f3",
    
    "model_xg_f1", 
    "model_xg_f2",
    "model_xg_f3",
    
    "model_gdt_f1",
    "model_gdt_f2",
    "model_gdt_f3"
])

In [83]:
for _ in range(2000):
    
    
    #decision_tree scikit
    model_dt = tree.DecisionTreeRegressor(random_state=_)
    model_dt.fit(X_train, y_train)
    explainer_dt = shap.Explainer(model_dt)
    shap_values_dt = explainer_dt(X_train)
    dt_feature_importances = list(np.average(np.abs(shap_values_dt.values), axis=0)[0:3])

    
    # random forest scikit
    model_rf = RandomForestRegressor(random_state=_)
    model_rf.fit(X_train, y_train)
    explainer_rf = shap.Explainer(model_rf)
    shap_values_rf = explainer_rf(X_train)
    rf_feature_importances = list(np.average(np.abs(shap_values_rf.values), axis=0)[0:3])
    
    # Extra Trees scikit
    model_et = ExtraTreesRegressor(random_state=_)
    model_et.fit(X_train, y_train)
    explainer_et = shap.Explainer(model_et)
    shap_values_et = explainer_et(X_train)
    et_feature_importances = list(np.average(np.abs(shap_values_et.values), axis=0)[0:3])

    
    #Catboost
    model_cat = CatBoostRegressor(silent=True, random_state=_)
    model_cat.fit(X_train, y_train)
    pooled_data = Pool(X_train)
    shap_values_cat = model_cat.get_feature_importance(pooled_data, type="ShapValues")
    cat_feature_importances = list(np.average(np.abs(shap_values_cat), axis=0)[0:3])
        
    #EBM
    model_ebm1 = ExplainableBoostingRegressor(interactions=0, random_state=_, outer_bags=1)
    model_ebm1.fit(X_train, y_train)
      
    model_ebm8 = ExplainableBoostingRegressor(interactions=0, random_state=_, outer_bags=8)
    model_ebm8.fit(X_train, y_train)
  
    model_ebm16 = ExplainableBoostingRegressor(interactions=0, random_state=_, outer_bags=16)
    model_ebm16.fit(X_train, y_train)
   
    model_ebm24 = ExplainableBoostingRegressor(interactions=0, random_state=_, outer_bags=24)
    model_ebm24.fit(X_train, y_train)
    
    #LightGBM
    model_lgb = LGBMRegressor(random_state=_)
    model_lgb.fit(X_train, y_train)
    explainer_lgb = shap.Explainer(model_lgb)
    shap_values_lgb = explainer_lgb(X_train)
    lgb_feature_importances = list(np.average(np.abs(shap_values_lgb.values), axis=0)[0:3])

    
    #XGBoost
    model_xg = XGBRegressor(random_state=_)
    model_xg.fit(X_train, y_train)
    explainer_xg = shap.Explainer(model_xg)
    shap_values_xg = explainer_xg(X_train)
    xg_feature_importances = list(np.average(np.abs(shap_values_xg.values), axis=0)[0:3])

    
    #GradientboostingRegressor scikit
    model_gdt = GradientBoostingRegressor(random_state=_)
    model_gdt.fit(X_train, y_train)   
    explainer_gdt = shap.Explainer(model_gdt)
    shap_values_gdt = explainer_gdt(X_train) 
    gdt_feature_importances = list(np.average(np.abs(shap_values_gdt.values), axis=0)[0:3])
    
    
    #creating series and adding series to df
    series = pd.Series(
        [
            dt_feature_importances[0],
            dt_feature_importances[1],
            dt_feature_importances[2],
            
            rf_feature_importances[0],
            rf_feature_importances[1],
            rf_feature_importances[2],
            
            et_feature_importances[0],
            et_feature_importances[1],
            et_feature_importances[2],
            
            cat_feature_importances[0],
            cat_feature_importances[1],
            cat_feature_importances[2],
            
            model_ebm1.feature_importances_[0],
            model_ebm1.feature_importances_[1],
            model_ebm1.feature_importances_[2],
            
            model_ebm8.feature_importances_[0],
            model_ebm8.feature_importances_[1],
            model_ebm8.feature_importances_[2],
            
            model_ebm16.feature_importances_[0],
            model_ebm16.feature_importances_[1],
            model_ebm16.feature_importances_[2],
            
            model_ebm24.feature_importances_[0],
            model_ebm24.feature_importances_[1],
            model_ebm24.feature_importances_[2],
            
            lgb_feature_importances[0],  
            lgb_feature_importances[1], 
            lgb_feature_importances[2],
            
            xg_feature_importances[0],
            xg_feature_importances[1],
            xg_feature_importances[2],
            
            gdt_feature_importances[0],
            gdt_feature_importances[1],
            gdt_feature_importances[2]

        ], index = df.columns           
    )
        
    df = df.append(
        series,
        ignore_index=True
    )

In [84]:
df

model_dt_f1  model_dt_f2  model_dt_f3  model_rf_f1  model_rf_f2  \
0       27.478373    36.611107    18.728476    15.642651    19.610595   
1       49.254214    13.121642    27.131317    18.483677    19.615866   
2       49.698451    13.480458    19.379820    15.760586    16.396465   
3       14.913437    19.676283    50.839190    17.517781    18.667762   
4       16.343170    22.476333    39.989633    17.380054    17.264620   
...           ...          ...          ...          ...          ...   
1995    20.168371    47.663034    14.225467    17.009580    17.335982   
1996    15.483956    14.121935    44.218469    15.097754    18.016080   
1997    44.836782    19.335647    14.541780    17.455163    16.959108   
1998    17.052360    29.714734    38.412481    16.497976    17.716781   
1999    13.999182    58.464577    19.746335    17.302739    15.162957   

      model_rf_f3  model_et_f1  model_et_f2  model_et_f3  model_cat_f1  ...  \
0       15.805876    18.520219    20.788251    21.031391     14.909151  ...   
1       13.501868    18.323742    21.044518    20.878179     14.005264  ...   
2       18.891354    20.631138    19.768238    19.738038     15.293730  ...   
3       15.809615    20.423411    19.291568    20.589270     15.661425  ...   
4       17.265697    21.648728    19.190071    19.429471     16.426581  ...   
...           ...          ...          ...          ...           ...  ...   
1995    16.521626    21.512395    20.646618    18.082478     16.303090  ...   
1996    18.203135    19.817347    19.461620    20.952471     16.268489  ...   
1997    17.892137    19.974369    21.857794    18.410371     15.988704  ...   
1998    17.643801    19.374468    20.053209    20.939787     18.318813  ...   
1999    18.379716    19.285445    21.635607    19.293999     16.031380  ...   

      model_ebm_f3_out_24  model_lgb_f1  model_lgb_f2  model_lgb_f3  \
0               12.535686     43.337481           0.0           0.0   
1               11.299288     43.337481           0.0           0.0   
2               12.453105     43.337481           0.0           0.0   
3               11.796268     43.337481           0.0           0.0   
4               12.236981     43.337481           0.0           0.0   
...                   ...           ...           ...           ...   
1995            13.089080     43.337481           0.0           0.0   
1996            12.602529     43.337481           0.0           0.0   
1997            11.696146     43.337481           0.0           0.0   
1998            12.363098     43.337481           0.0           0.0   
1999            12.701754     43.337481           0.0           0.0   

      model_xg_f1  model_xg_f2  model_xg_f3  model_gdt_f1  model_gdt_f2  \
0       59.272648          0.0          0.0     22.536200     18.016643   
1       59.272648          0.0          0.0     18.627454     21.724226   
2       59.272648          0.0          0.0     14.818871     12.474762   
3       59.272648          0.0          0.0     12.882206     15.009386   
4       59.272648          0.0          0.0     24.011544     15.047527   
...           ...          ...          ...           ...           ...   
1995    59.272648          0.0          0.0     21.931456     16.002387   
1996    59.272648          0.0          0.0     11.620316     18.315579   
1997    59.272648          0.0          0.0     17.566890     16.812361   
1998    59.272648          0.0          0.0     23.220008     18.315378   
1999    59.272648          0.0          0.0     18.467136     16.453914   

      model_gdt_f3  
0        11.381253  
1        11.158541  
2        26.041010  
3        25.767141  
4        12.279320  
...            ...  
1995     12.589895  
1996     19.957786  
1997     15.754548  
1998      9.508741  
1999     15.644089  

[2000 rows x 33 columns]

In [85]:
df.to_csv("models_collinearity_shap.csv", index=False)

In [86]:
data_full = pd.read_csv("models_collinearity_shap.csv")

In [87]:
data_full

model_dt_f1  model_dt_f2  model_dt_f3  model_rf_f1  model_rf_f2  \
0       27.478373    36.611107    18.728476    15.642651    19.610595   
1       49.254214    13.121642    27.131317    18.483677    19.615866   
2       49.698451    13.480458    19.379820    15.760586    16.396465   
3       14.913437    19.676283    50.839190    17.517781    18.667762   
4       16.343170    22.476333    39.989633    17.380054    17.264620   
...           ...          ...          ...          ...          ...   
1995    20.168371    47.663034    14.225467    17.009580    17.335982   
1996    15.483956    14.121935    44.218469    15.097754    18.016080   
1997    44.836782    19.335647    14.541780    17.455163    16.959108   
1998    17.052360    29.714734    38.412481    16.497976    17.716781   
1999    13.999182    58.464577    19.746335    17.302739    15.162957   

      model_rf_f3  model_et_f1  model_et_f2  model_et_f3  model_cat_f1  ...  \
0       15.805876    18.520219    20.788251    21.031391     14.909151  ...   
1       13.501868    18.323742    21.044518    20.878179     14.005264  ...   
2       18.891354    20.631138    19.768238    19.738038     15.293730  ...   
3       15.809615    20.423411    19.291568    20.589270     15.661425  ...   
4       17.265697    21.648728    19.190071    19.429471     16.426581  ...   
...           ...          ...          ...          ...           ...  ...   
1995    16.521626    21.512395    20.646618    18.082478     16.303090  ...   
1996    18.203135    19.817347    19.461620    20.952471     16.268489  ...   
1997    17.892137    19.974369    21.857794    18.410371     15.988704  ...   
1998    17.643801    19.374468    20.053209    20.939787     18.318813  ...   
1999    18.379716    19.285445    21.635607    19.293999     16.031380  ...   

      model_ebm_f3_out_24  model_lgb_f1  model_lgb_f2  model_lgb_f3  \
0               12.535686     43.337481           0.0           0.0   
1               11.299288     43.337481           0.0           0.0   
2               12.453105     43.337481           0.0           0.0   
3               11.796268     43.337481           0.0           0.0   
4               12.236981     43.337481           0.0           0.0   
...                   ...           ...           ...           ...   
1995            13.089080     43.337481           0.0           0.0   
1996            12.602529     43.337481           0.0           0.0   
1997            11.696146     43.337481           0.0           0.0   
1998            12.363098     43.337481           0.0           0.0   
1999            12.701754     43.337481           0.0           0.0   

      model_xg_f1  model_xg_f2  model_xg_f3  model_gdt_f1  model_gdt_f2  \
0       59.272648          0.0          0.0     22.536200     18.016643   
1       59.272648          0.0          0.0     18.627454     21.724226   
2       59.272648          0.0          0.0     14.818871     12.474762   
3       59.272648          0.0          0.0     12.882206     15.009386   
4       59.272648          0.0          0.0     24.011544     15.047527   
...           ...          ...          ...           ...           ...   
1995    59.272648          0.0          0.0     21.931456     16.002387   
1996    59.272648          0.0          0.0     11.620316     18.315579   
1997    59.272648          0.0          0.0     17.566890     16.812361   
1998    59.272648          0.0          0.0     23.220008     18.315378   
1999    59.272648          0.0          0.0     18.467136     16.453914   

      model_gdt_f3  
0        11.381253  
1        11.158541  
2        26.041010  
3        25.767141  
4        12.279320  
...            ...  
1995     12.589895  
1996     19.957786  
1997     15.754548  
1998      9.508741  
1999     15.644089  

[2000 rows x 33 columns]

In [88]:
model_names= [
    "scikit-Decision Tree",
    "scikit-Random Forest",
    "scikit-ExtraTrees",
    "Catboost",
    "EBM_1",
    "EBM_8",
    "EBM_16",
    "EBM_24",
    "Lightgbm",
    "XGBoost",
    "scikit-GradienboostingTree"
]

model_list = [
    "model_dt_f1", 
    "model_dt_f2",
    "model_dt_f3",
    
    "model_rf_f1", 
    "model_rf_f2",
    "model_rf_f3",
    
    "model_et_f1", 
    "model_et_f2",
    "model_et_f3",
    
    "model_cat_f1",
    "model_cat_f2",
    "model_cat_f3",
    
    "model_ebm_f1_out_1",
    "model_ebm_f2_out_1",
    "model_ebm_f3_out_1",
    
    "model_ebm_f1_out_8",
    "model_ebm_f2_out_8",
    "model_ebm_f3_out_8",
    
    "model_ebm_f1_out_16",
    "model_ebm_f2_out_16",
    "model_ebm_f3_out_16",
    
    "model_ebm_f1_out_24",
    "model_ebm_f2_out_24",
    "model_ebm_f3_out_24",
    
    "model_lgb_f1",
    "model_lgb_f2",
    "model_lgb_f3",
    
    "model_xg_f1",
    "model_xg_f2",
    "model_xg_f3",
    
    "model_gdt_f1",
    "model_gdt_f2",
    "model_gdt_f3"]

In [90]:
names_index = 0
for _ in range(0, len(model_list), 3):
    fig = px.scatter(width=2000, height=800)
    fig.add_trace(go.Scatter(y=data_full[model_list[_]] , x=data_full.index, name='Feature 1', mode='markers'))
    fig.add_trace(go.Scatter(y=data_full[model_list[_+1]], x=data_full.index,  name='Feature 2', mode='markers'))
    fig.add_trace(go.Scatter(y=data_full[model_list[_+2]], x=data_full.index,  name='Feature 3', mode='markers'))
    print(data_full[model_list[_]].name)
    print(data_full[model_list[_+1]].name)
    print(data_full[model_list[_+2]].name)
    fig.update_layout(
        title=model_names[names_index], 
        xaxis_title="Random Seeds",
        yaxis_title="Feature Importance"
    )
    
    fig.update_layout(hovermode="x")

    fig.show()
    fig.write_html(f"{model_names[names_index]}.html")
    names_index += 1
    

model_dt_f1
model_dt_f2
model_dt_f3


model_rf_f1
model_rf_f2
model_rf_f3


model_et_f1
model_et_f2
model_et_f3


model_cat_f1
model_cat_f2
model_cat_f3


model_ebm_f1_out_1
model_ebm_f2_out_1
model_ebm_f3_out_1


...

model_ebm_f1_out_24
model_ebm_f2_out_24
model_ebm_f3_out_24


model_lgb_f1
model_lgb_f2
model_lgb_f3


model_xg_f1
model_xg_f2
model_xg_f3


model_gdt_f1
model_gdt_f2
model_gdt_f3


IndexError: list index out of range